Constants

In [3]:
input_dir = "plant_disease_dataset"
train_dir = input_dir + '/train'
valid_dir = input_dir +'/valid'

Use imagefolder to digest images from train and test datasets

In [4]:
from torchvision.datasets import ImageFolder
import torchvision.transforms as transforms
from torch.utils.data import DataLoader
import torch
import torch
import torch.nn as nn
import torch.optim as optim
import time
import numpy as np

In [5]:
transform = transforms.Compose([
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
])

In [6]:
train_images = ImageFolder(train_dir,transform = transform)
valid_images = ImageFolder(valid_dir,transform = transform)

In [7]:
img, label = train_images[5000]
# print(img.shape, label)
# print(train_images.classes)
# print(valid_images.classes)

In [8]:
images_train_list = []
labels_train = []
for image,label in train_images:
    images_train_list.append(image)
    labels_train.append(label)

images_train_tensors = torch.stack(images_train_list)
labels_train_tensor = torch.tensor(labels_train)

images_test_list = []
labels_test = []
for image,label in valid_images:
    images_test_list.append(image)
    labels_test.append(label)

images_test_tensors = torch.stack(images_test_list)
labels_test_tensor = torch.tensor(labels_test)


In [9]:
num_trainimages=(len(train_images))

In [12]:
flattened_images = images_train_tensors.view(num_trainimages, -1).numpy()  # Shape will be (7000, 3*256*256)
labels_train = np.array(labels_train_tensor)

In [ ]:
flattened_images_test = images_test_tensors.view(num_test_images, -1).numpy()  # Shape will be (7000, 3*256*256)
labels_test = np.array(labels_test_tensor)

# Neural Network

In [36]:
class NeuralNet(nn.Module):
    def __init__(self, 
                 #input_size=3 * 256 * 256, 
                 num_classes=4):
        super(NeuralNet, self).__init__()
        self.conv1 = nn.Conv2d(3, 16, kernel_size=3, stride=1, padding=1)
        self.conv2 = nn.Conv2d(16, 32, kernel_size=3, stride=1, padding=1)
        self.conv3 = nn.Conv2d(32, 64, kernel_size=3, stride=1, padding=1)
        self.pool = nn.MaxPool2d(kernel_size=2, stride=2, padding=0)
        self.fc1 = nn.Linear(64 * 32 * 32, 128)
        self.fc2 = nn.Linear(128, num_classes)

    def forward(self, x):
        x = self.pool(torch.relu(self.conv1(x)))
        x = self.pool(torch.relu(self.conv2(x)))
        x = self.pool(torch.relu(self.conv3(x)))
        x = x.view(-1, 64 * 32 * 32)
        x = torch.relu(self.fc1(x))
        x = self.fc2(x)
        return x


In [103]:
loss_fun = nn.CrossEntropyLoss()
n_epochs = 20
batch_size = 32
train_accuracy_list = []
test_accuracy_list = []
training_time_list = []
pct_of_train_data = []
epoch_loss_list = []

In [105]:

for i in np.linspace(0.1, 1.0, 10):
    print('training', i, 'of data')
    epoch_loss_this_iter = []
    start = time.time()
    model = NeuralNet()
    optimizer=optim.Adam(model.parameters(),lr=0.001)
    num_trainimages_this_iter = int(num_trainimages*i)
    print(num_trainimages_this_iter)
    for epoch in range(n_epochs):
        loss = 0
        for i in range(0,num_trainimages_this_iter,batch_size):
            inputs = images_train_tensors[i:i+batch_size]
            labels = labels_train_tensor[i:i+batch_size]
            optimizer.zero_grad()
            outputs=model(inputs)
            batch_loss = loss_fun(outputs,labels)

            batch_loss.backward()
            optimizer.step()

            loss+=batch_loss
        epoch_loss_this_iter.append(loss)
    
    epoch_loss_list.append(epoch_loss_this_iter)
    print('epoch losses',epoch_loss_list)
    training_time_list.append(time.time()-start)
    


    # Evaluate the model
    model.eval()
    # on train dataset 
    correct = 0
    total = 0
    with torch.no_grad():
        for i in range(0, num_trainimages_this_iter, batch_size):
            inputs = images_train_tensors[i:i+batch_size]
            labels = labels_train_tensor[i:i+batch_size]
            outputs = model(inputs)
            # print(outputs)
            
            _, predicted = torch.max(outputs.data, 1)
            total += labels.size(0)
            correct += (predicted == labels).sum().item()
        print(correct,total)
        train_accuracy_list.append(correct/total)
    
    # on test dataset 
    correct = 0
    total = 0
    with torch.no_grad():
        for i in range(0, len(images_test_tensors), batch_size):
            inputs = images_test_tensors[i:i+batch_size]
            labels = labels_test_tensor[i:i+batch_size]
            outputs = model(inputs)
            # print(outputs)
            
            _, predicted = torch.max(outputs.data, 1)
            total += labels.size(0)
            correct += (predicted == labels).sum().item()
        test_accuracy_list.append(correct/total)
        print(correct,total)
    
    pct_of_train_data.append(int(i*100))


    del model 
    
    

training 0.1 of data
777
epoch losses [tensor(1.3314, grad_fn=<AddBackward0>), tensor(1.3314, grad_fn=<AddBackward0>), tensor(1.3314, grad_fn=<AddBackward0>), tensor(1.3314, grad_fn=<AddBackward0>), tensor(1.3314, grad_fn=<AddBackward0>), tensor(1.3314, grad_fn=<AddBackward0>), tensor(1.3314, grad_fn=<AddBackward0>), tensor(1.3314, grad_fn=<AddBackward0>), tensor(1.3314, grad_fn=<AddBackward0>), tensor(1.3314, grad_fn=<AddBackward0>), tensor(1.3314, grad_fn=<AddBackward0>), tensor(1.3314, grad_fn=<AddBackward0>), tensor(1.3314, grad_fn=<AddBackward0>), tensor(1.3314, grad_fn=<AddBackward0>), tensor(1.3314, grad_fn=<AddBackward0>), tensor(1.3314, grad_fn=<AddBackward0>), tensor(1.3314, grad_fn=<AddBackward0>), tensor(1.3314, grad_fn=<AddBackward0>), tensor(1.3314, grad_fn=<AddBackward0>), tensor(1.3314, grad_fn=<AddBackward0>), tensor(1.3314, grad_fn=<AddBackward0>), tensor(1.3314, grad_fn=<AddBackward0>), tensor(1.3314, grad_fn=<AddBackward0>), tensor(1.3314, grad_fn=<AddBackward0>), t

KeyboardInterrupt: 

In [95]:
len(images_test_tensors)

1943

In [83]:

for epoch in range(n_epochs):
    loss = 0
    for i in range(0,num_trainimages,batch_size):
        inputs = images_train_tensors[i:i+batch_size]
        labels = labels_train_tensor[i:i+batch_size]
        optimizer.zero_grad()
        outputs=model(inputs)
        batch_loss = loss_fun(outputs,labels)

        batch_loss.backward()
        optimizer.step()

        loss+=batch_loss


    print(f'[Epoch {epoch + 1}, loss {loss}')

        
        
print('Finished Training')

[Epoch 1, loss 314.4078063964844
[Epoch 2, loss 365.4493713378906
[Epoch 3, loss 342.6195373535156
[Epoch 4, loss 219.22000122070312
[Epoch 5, loss 210.58419799804688
[Epoch 6, loss 258.3178405761719
[Epoch 7, loss 314.41229248046875
[Epoch 8, loss 238.5794677734375
[Epoch 9, loss 234.33192443847656
[Epoch 10, loss 196.87545776367188
[Epoch 11, loss 240.14923095703125
[Epoch 12, loss 150.02061462402344
[Epoch 13, loss 213.5911102294922
[Epoch 14, loss 168.1241912841797
[Epoch 15, loss 198.3705596923828
[Epoch 16, loss 173.691162109375
[Epoch 17, loss 176.49362182617188
[Epoch 18, loss 167.45632934570312
[Epoch 19, loss 156.11033630371094
[Epoch 20, loss 154.32574462890625
[Epoch 21, loss 179.0638885498047
[Epoch 22, loss 173.18397521972656
[Epoch 23, loss 154.7816619873047
[Epoch 24, loss 146.0135040283203
[Epoch 25, loss 143.828369140625
[Epoch 26, loss 136.75962829589844
[Epoch 27, loss 132.47161865234375
[Epoch 28, loss 124.25160217285156
[Epoch 29, loss 125.05320739746094
[Epoch 30

In [39]:
num_trainimages

7771

In [84]:
from torchsummary import summary

# Replace (3, 256, 256) with the input size of your model
summary(model, (3, 256, 256))

----------------------------------------------------------------
        Layer (type)               Output Shape         Param #
            Conv2d-1         [-1, 16, 256, 256]             448
         MaxPool2d-2         [-1, 16, 128, 128]               0
            Conv2d-3         [-1, 32, 128, 128]           4,640
         MaxPool2d-4           [-1, 32, 64, 64]               0
            Conv2d-5           [-1, 64, 64, 64]          18,496
         MaxPool2d-6           [-1, 64, 32, 32]               0
            Linear-7                  [-1, 128]       8,388,736
            Linear-8                    [-1, 4]             516
Total params: 8,412,836
Trainable params: 8,412,836
Non-trainable params: 0
----------------------------------------------------------------
Input size (MB): 0.75
Forward/backward pass size (MB): 17.50
Params size (MB): 32.09
Estimated Total Size (MB): 50.34
----------------------------------------------------------------


In [85]:
for name, param in model.named_parameters():
    print(f'Parameter: {name}')
    print(param)
    print('---')

Parameter: conv1.weight
Parameter containing:
tensor([[[[-3.0057e-02, -1.7388e-01, -1.1170e-01],
          [-8.3699e-02, -8.2292e-02,  2.2466e-01],
          [ 4.6438e-03, -1.7071e-01,  2.1781e-01]],

         [[-4.1577e-02, -2.0520e-01,  3.1841e-03],
          [ 1.6700e-01,  1.7672e-01,  1.3362e-01],
          [-1.6539e-01, -2.0241e-01,  1.9354e-01]],

         [[ 6.9039e-02, -2.5123e-02,  2.5115e-02],
          [-1.0957e-01,  2.3384e-02,  1.7078e-01],
          [-9.9286e-02,  1.3560e-02, -2.4789e-02]]],


        [[[ 1.7166e-01,  1.6538e-01,  2.3747e-02],
          [-2.1667e-02,  9.8545e-02,  1.4962e-01],
          [ 1.6115e-01,  1.9236e-01,  1.2244e-01]],

         [[-1.7287e-01,  7.6661e-02, -1.9874e-01],
          [-7.9007e-03,  3.5158e-02, -2.1701e-01],
          [ 4.8095e-02, -1.4320e-01, -1.1965e-01]],

         [[-2.2718e-01,  8.7032e-02, -2.4584e-02],
          [-1.5418e-01,  6.9550e-02,  9.8158e-02],
          [-4.3924e-02,  8.0367e-02,  9.4456e-03]]],


        [[[ 5.3604e-

## testing on validation set

tensor([[[-2.0665, -0.3712, -0.3883,  ...,  0.7933,  0.8104,  0.8276],
         [-2.0665, -0.3712, -0.3712,  ...,  0.7762,  0.7933,  0.8104],
         [-2.0665, -0.3541, -0.3541,  ...,  0.7419,  0.7591,  0.7762],
         ...,
         [-1.9638, -0.0287, -0.0116,  ...,  1.0844,  1.0844,  1.0844],
         [-1.9295, -0.0116, -0.0116,  ...,  1.0673,  1.0673,  1.0673],
         [-1.8953, -0.0116, -0.0116,  ...,  1.0673,  1.0502,  1.0502]],

        [[-2.0357, -0.3901, -0.4251,  ...,  0.8704,  0.8880,  0.9055],
         [-2.0357, -0.3901, -0.4076,  ...,  0.8529,  0.8704,  0.8880],
         [-2.0357, -0.3725, -0.3901,  ...,  0.8179,  0.8354,  0.8529],
         ...,
         [-2.0357, -0.1625, -0.1450,  ...,  1.1856,  1.1856,  1.1856],
         [-2.0357, -0.1450, -0.1450,  ...,  1.1681,  1.1681,  1.1681],
         [-2.0357, -0.1450, -0.1450,  ...,  1.1681,  1.1506,  1.1506]],

        [[-1.4733,  0.2522,  0.2696,  ...,  1.6640,  1.6814,  1.6988],
         [-1.4733,  0.2522,  0.2871,  ...,  1

In [87]:
# Evaluate the model
model.eval()
correct = 0
total = 0
with torch.no_grad():
    for i in range(0, len(images_test_tensors), batch_size):
        inputs = images_test_tensors[i:i+batch_size]
        labels = labels_test_tensor[i:i+batch_size]
        outputs = model(inputs)
        print(outputs)
        
        _, predicted = torch.max(outputs.data, 1)
        total += labels.size(0)
        correct += (predicted == labels).sum().item()

tensor([[ 5.5426e-02, -2.1115e+01, -4.3090e+01, -3.3213e+01],
        [ 8.7922e+00, -5.7950e+00, -3.5097e+01, -4.2875e+01],
        [ 8.4321e+00, -2.5737e+01, -1.7753e+01, -5.3701e+01],
        [ 6.7127e+00, -2.5534e+01, -4.2209e+01, -2.9650e+01],
        [-4.5270e+00, -1.8755e+00, -4.8218e+01, -3.2629e+01],
        [ 2.2343e+00, -2.9790e+01, -4.9824e+01, -2.1298e+01],
        [ 1.4754e+01, -1.7917e+01, -4.2671e+01, -4.2974e+01],
        [ 1.0002e+01, -2.4519e+01, -7.9097e+00, -3.4957e+01],
        [ 1.4998e+01, -2.6275e+01,  4.5382e+00, -5.1703e+01],
        [ 5.1183e+00, -2.9286e+01, -1.1755e+01, -2.4440e+01],
        [ 2.0425e+01, -1.7555e+01, -4.2883e+01, -4.2610e+01],
        [ 6.0540e+00, -1.1087e+01, -4.7728e+01, -3.5920e+01],
        [ 5.6056e+00, -2.3357e+01, -2.1699e+01, -2.0426e+01],
        [ 2.6214e+00, -2.7374e+01, -2.0171e+01, -2.8618e+01],
        [-1.4245e+00, -3.9076e+01, -5.5531e+01, -2.9013e+01],
        [ 9.9168e+00, -3.2190e+01, -5.5510e+01, -3.3258e+01],
        

In [88]:
print(f'Accuracy: {100 * correct / total}%')

Accuracy: 97.47812660833762%


In [44]:
outputs

tensor([[-0.2968, -0.1493, -0.1045,  0.1410],
        [-0.2968, -0.1493, -0.1045,  0.1410],
        [-0.2968, -0.1493, -0.1045,  0.1410],
        ...,
        [-0.2968, -0.1493, -0.1045,  0.1410],
        [-0.2968, -0.1493, -0.1045,  0.1410],
        [-0.2968, -0.1493, -0.1045,  0.1410]])

# KNN

In [14]:
print(images_train_tensors.size())
print(labels_train_tensor.size())

torch.Size([7771, 3, 256, 256])
torch.Size([7771])


In [15]:
import torch
import numpy as np
from sklearn.neighbors import KNeighborsClassifier

In [17]:
flattened_images = images_train_tensors.view(num_trainimages, -1).numpy()  # Shape will be (7000, 3*256*256)
labels_train = np.array(labels_train_tensor)

In [18]:
print(flattened_images.shape)
print(labels_train.shape)

(7771, 196608)
(7771,)


In [19]:
train_accuracy_list = []
test_accuracy_list = []
training_time_list = []
pct_of_train_data = []
epoch_loss_list = []

In [20]:
for i in np.linspace(0.1, 1.0, 10):
    knn = KNeighborsClassifier(n_neighbors=4)  
    train = flattened_images[:int(i*len(flattened_images))]
    train_labels = labels_train[:int(i*len(flattened_images))]
    knn.fit(train, train_labels)
    predictions = knn.predict(train)
    train_accuracy_list.append((predictions==train_labels).mean())

    num_test_images = len(images_test_list)
    flattened_images_test = images_test_tensors.view(num_test_images, -1).numpy()  # Shape will be (7000, 3*256*256)
    labels_test = np.array(labels_test_tensor)
    predictions = knn.predict(flattened_images_test)
    test_accuracy_list.append((predictions==labels_test).mean())

    pct_of_train_data.append(i)
    print('finished', i)





finished 0.1
finished 0.2
finished 0.30000000000000004
finished 0.4
finished 0.5
finished 0.6
finished 0.7000000000000001
finished 0.8
finished 0.9
finished 1.0


In [22]:
train_accuracy_list

[1.0,
 1.0,
 0.8914628914628915,
 0.8227155727155727,
 0.8051480051480051,
 0.8108108108108109,
 0.8075013789299503,
 0.7818532818532818,
 0.7853567853567853,
 0.7983528503410114]

In [21]:
train_accuracy_list
test_accuracy_list

[0.25939269171384455,
 0.25939269171384455,
 0.301080802882141,
 0.3587236232629954,
 0.3870303654143078,
 0.5486361296963459,
 0.5270200720535255,
 0.6176016469377251,
 0.6685537828100875,
 0.6870818322182193]

In [66]:
# Initialize KNN classifier
knn = KNeighborsClassifier(n_neighbors=4)  
# Fit the KNN model
knn.fit(flattened_images, labels_train)

KNeighborsClassifier(n_neighbors=4)

## test on valid set

In [75]:
num_test_images = len(images_test_list)
flattened_images_test = images_test_tensors.view(num_test_images, -1).numpy()  # Shape will be (7000, 3*256*256)
labels_test = np.array(labels_test_tensor)
predictions = knn.predict(flattened_images_test)

In [76]:
(predictions==labels_test).mean()

0.6870818322182193

# SVM

In [10]:
from sklearn.svm import SVC
from sklearn.metrics import accuracy_score

In [11]:
train_accuracies = []
test_accuracies = []
max_iter=100

for i in range(1, max_iter + 1):
    svm = SVC(kernel='linear')  # You can choose different kernels such as 'linear', 'rbf', etc.
    svm.max_iter = i
    svm.fit(flattened_images, labels_train)
    
    # Predict on train and test data
    y_train_pred = svm.predict(flattened_images)
    y_test_pred = svm.predict(flattened_images_test)
    
    # Calculate accuracy
    train_acc = accuracy_score(labels_train, y_train_pred)
    test_acc = accuracy_score(labels_test, y_test_pred)
    
    train_accuracies.append(train_acc)
    test_accuracies.append(test_acc)
    print('finished',i)
    del svm

NameError: name 'flattened_images' is not defined

In [81]:
# Initialize SVM classifier
svm = SVC(kernel='linear')  # You can choose different kernels such as 'linear', 'rbf', etc.

# Fit the SVM model
svm.fit(flattened_images, labels_train)


# Predict the labels
predictions = svm.predict(flattened_images_test)
(predictions==labels_test).mean()

0.9068450849202264